# 4.1 模型微调VS指令微调

## 一个典型的知乎问题

### **问题**

用LLM实现文本二分类，微调base模型还是微调chat模型比较好？[问题](https://www.zhihu.com/question/632473480/answer/38930949853)

我想用开源LLM（例如chatglm，baichuan）实现文本二分类（比如正负情感分类），有一组训练数据可以用于微调模型，提升分类性能，这时候应该选择base模型还是chat模型？


### **回答**
1 如果是使用2分类的header，base模型好一些。

也就是使用如下类似的的设置。

model = AutoModelForSequenceClassification.from_pretrained(
"yuanzhoulvpi/gpt2_chinese", num_labels=2
)

对应的训练数据一般是这样的：

| seq                          | label |
|------------------------------|-------|
| 他家的奶茶超级好喝。。。      | 1     |
| 他家的奶茶超级难喝。。。      | 0     |


2 如果是把分类问题，改成指令微调的模式，就是像

```
{

"instruction": "你现在在做一项情感分类的任务，如果是积极情感，则回答积极。消极情感则回答消极。"
"input"：他家的奶茶超级好喝。。。
"output"：“积极”

}
```

然后进行指令微调，lora/peft调整部分参数就行，一般是chat模型比较好。



这种二分类问题，用llm就是大材小用了，一般就是选个小的的模型，用AutoModelForSequenceClassification效果最好，如果追求SOTA，有些研究表明搞成指令微调模式效果可能更好。

## 大模型微调（Fine-tuning）和指令微调（Instruction Tuning）

普通的大模型微调（Fine-tuning）和指令微调（Instruction Tuning）是两种不同的训练方法，它们适用于不同的应用场景，并且在实现细节上也有所区别。


#### 1. **定义**

普通微调是指在一个预训练好的大模型基础上，针对特定任务添加一个或多个新层（通常称为头部或 header），然后使用特定任务的数据集对整个模型（包括新添加的层）进行再训练的过程。对于分类任务，常见的做法是在 GPT-2 的顶部添加一个分类头。

#### 2. **具体步骤**

- **添加分类头**：为 GPT-2 添加一个分类头，该头通常包含线性层（全连接层）以及可能的激活函数和归一化层。
  
- **准备数据**：准备好用于微调的任务特定数据集，如文本分类、情感分析等。
  
- **微调过程**：
  - 使用任务特定的数据集对整个模型（包括预训练权重和新添加的分类头）进行再训练。
  - 通常会调整学习率、批量大小等超参数以优化性能。
  - 可能只对新添加的层进行训练，或者对整个模型进行微调（取决于资源和需求）。

#### 3. **适用场景**

- **任务明确**：当有清晰的任务目标时，例如文本分类、命名实体识别等。
- **标签数据可用**：拥有足够的标注数据来进行监督学习。

#### 4. **优点**

- **针对性强**：能够有效地提升模型在特定任务上的表现。
- **资源利用效率高**：相比于从头开始训练，微调需要的计算资源和时间较少。

#### 5. **缺点**

- **泛化能力有限**：微调后的模型可能在未见过的任务或领域中表现不佳。

### 指令微调（Instruction Tuning）

#### 1. **定义**

指令微调是一种更为通用的微调方法，它旨在让模型理解和遵循自然语言指令，而不是直接针对某个特定任务进行优化。这种方法通过提供一系列指令-输出对来训练模型，使其学会根据指令生成适当的响应。

#### 2. **具体步骤**

- **构造指令数据集**：创建一个包含各种指令及其预期输出的数据集。这些指令可以覆盖多种任务类型，如问答、翻译、摘要生成等。
  
- **微调过程**：
  - 使用指令数据集对模型进行训练，使模型能够理解并执行不同类型的指令。
  - 强调模型对自然语言指令的理解和执行，而非特定于某一任务的优化。

#### 3. **适用场景**

- **多任务适应**：当希望模型能够在多种不同类型的任务中表现出色时。
- **少样本学习**：在仅有少量示例的情况下，仍然可以让模型快速适应新任务。

#### 4. **优点**

- **灵活性高**：模型可以在没有额外训练的情况下处理新的任务。
- **跨领域泛化能力强**：更有可能在未曾见过的任务或领域中保持良好的性能。

#### 5. **缺点**

- **复杂度增加**：指令微调通常涉及更多的训练数据和更复杂的训练过程。
- **评估难度较大**：由于任务的多样性，评估模型性能变得更加困难。


### 小结

普通微调侧重于提高模型在特定任务上的性能，而指令微调则更加注重模型对自然语言指令的理解和执行能力。选择哪种方法取决于你的具体需求和应用场景。如果你有一个明确的任务并且有大量的标注数据，那么普通微调可能是更好的选择；如果你希望模型具有更高的灵活性和跨任务适应能力，则可以考虑指令微调。

## 从GPT到chatGPT

关键点在于指令微调（Instruction Tuning）
* 将所有任务统一为指令形式
* 多任务精调
* 与人类对齐（多样性）
* 进一步分为有监督指令微调和带有人类反馈的强化学习(RLHF)

告别微调

因为GPT-3使用了天量级的数据来进行预训练，所以学到的知识也更多更通用，以致于GPT-3打出的口号就是“告别微调的GPT-3”。

相比于BERT这种预训练+微调的两阶段模型，GPT-3的目标是模型更加通用，从而解决BERT这种下游任务微调需要依赖领域标注数据的情况。

拿我们实际业务举例，我主要做分本分类任务。对于使用BERT来完成文本分类任务来说，首先我需要使用海量的无标注文本数据进行预训练学习语言学知识。

幸运的是这种预训练过程一般是一次性的，训练完成后可以把模型保存下来继续使用。很多大厂比如谷歌、Facebook等把得到的预训练模型开源了出来，所以咱们只需要导入预训练好的模型权重就可以直接使用了，相当于完成了模型的预训练过程；第二阶段就是微调了，对于文本分类等下游任务来说， 我们需要一批带标签的训练语料来微调模型。不同的下游任务会需要特定的训练语料。这时候面临的一个最大的问题是训练语料是需要人工标注的，而标注的成本是非常高的。除此之外不同的标注人员因为经验阅历等不同导致对同一条文本的理解也不同，所以容易出现标注不一致的问题。当标注数据量较少时还容易出现模型过拟合。归根结底就是微调是需要标注数据的，而获取标注数据的成本是很高的。

为了解决这个问题，GPT-3可以让NLPer不用标注训练语料就能很好的完成下游任务，让GPT-3更通用更便利。GPT-3不需要进行微调的结构图如下所示：

<img src='img/sft.png' width='600px' />

## 指令微调数据构建

<img src='img/sft2.png' width='800px' />



根据典型的分类语料数据，构建指令微调数据

目前如llama等都使用Alpaca格式

指令数据当做一般的文本，进行无监督的训练，和预训练流程一致

In [1]:
import subprocess
import os
# 设置环境变量, autodl一般区域
result = subprocess.run('bash -c "source /etc/network_turbo && env | grep proxy"', shell=True, capture_output=True, text=True)
output = result.stdout
for line in output.splitlines():
    if '=' in line:
        var, value = line.split('=', 1)
        os.environ[var] = value

In [2]:
#原始模型
from transformers import AutoModel
model = AutoModel.from_pretrained("gpt2")
model

GPT2Model(
  (wte): Embedding(50257, 768)
  (wpe): Embedding(1024, 768)
  (drop): Dropout(p=0.1, inplace=False)
  (h): ModuleList(
    (0-11): 12 x GPT2Block(
      (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (attn): GPT2SdpaAttention(
        (c_attn): Conv1D(nf=2304, nx=768)
        (c_proj): Conv1D(nf=768, nx=768)
        (attn_dropout): Dropout(p=0.1, inplace=False)
        (resid_dropout): Dropout(p=0.1, inplace=False)
      )
      (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (mlp): GPT2MLP(
        (c_fc): Conv1D(nf=3072, nx=768)
        (c_proj): Conv1D(nf=768, nx=3072)
        (act): NewGELUActivation()
        (dropout): Dropout(p=0.1, inplace=False)
      )
    )
  )
  (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
)

In [3]:
#分类微调模型
from transformers import AutoModelForSequenceClassification
ft_model = AutoModelForSequenceClassification.from_pretrained("gpt2", num_labels=2)
ft_model

Some weights of GPT2ForSequenceClassification were not initialized from the model checkpoint at gpt2 and are newly initialized: ['score.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


GPT2ForSequenceClassification(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2SdpaAttention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (score): Linear(in_features=768, out_features=2, bias=False)
)

In [5]:
#指令微调模型
from transformers import AutoModelForCausalLM
sft_model = AutoModelForCausalLM.from_pretrained("gpt2")
sft_model

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2SdpaAttention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50257, bias=False)
)

In [6]:
from transformers import GPT2LMHeadModel
gpt2_model = GPT2LMHeadModel.from_pretrained("gpt2")
gpt2_model

GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(50257, 768)
    (wpe): Embedding(1024, 768)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2SdpaAttention(
          (c_attn): Conv1D(nf=2304, nx=768)
          (c_proj): Conv1D(nf=768, nx=768)
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=3072, nx=768)
          (c_proj): Conv1D(nf=768, nx=3072)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=768, out_features=50257, bias=False)
)